# Progetto AIMAG

L’obiettivo degli algoritmi di **anomaly detection** è quello di individuare se ci sono delle anomalie di comportamento da parte dell’applicazione che si sta analizzando. Nel contesto industriale l’obiettivo è quello di identificare in maniera automatica:

1. Condizioni di setup/avviamento dei macchinari
2. Anomalie e sbalzi nei valori osservati, in modo tale da poter avvertire l'operatore di un eventuale guasto e/o risultato sbagliato nella produzione rispetto a una condizione normale della macchina.
3. Cambi di stato dovuti a un deterioramento dei componenti o a un diverso setting della macchina 


Più in generale, molte applicazioni richiedono la capacità di decidere se una nuova osservazione appartiene alla stessa distribuzione che si sta osservando (“inlier”), oppure no (“outlier”), le tecniche in grado di farlo prendono il nome di Anomaly Detection e si dividono in due categorie:

1. **Outlier Detection**: metodo unsupervised in cui si identificano gli outlier come deviazioni nei dati, andando a identificare le regioni più concentrate e segnalando eventuali scostamenti.
2. **Novelty Detection**: metodo semi-supervised in cui si cerca di imparare un comportamento/storia nei dati con l’obiettivo di identificare nelle nuove osservazioni un eventuale scostamento dal comportamento normale imparato.


I metodi di anomaly detection imparano durante il training una rappresentazione delle operazioni normali del macchinario, le quali vengono usate per identificare deviazioni dal comportamento normale codificato. Successivamente durante la fase di test, i modelli allenati assegnano un score a ogni dato di test per identificare se i record appartengono a una condizione normale o anomala.

In particolare, in questo esempio vedremo un applicazione degli algoritmi di **Deep Learning** per identificare le anomalie presenti, detti AutoEncoder. Gli **AutoEncoder** sono delle architetture basate su reti neurali che comprimono il file in una rappresentazione vettoriale compatta (fase di encoding) e ricostruiscono poi i dati originali a partire da questa rappresentazione intermedia (fase di decoding). Nel contesto della anomaly detection, queste architetture permettono di identificare nuove condizioni operative, quelle in cui l'errore di ricostruzione ottenuto supera una certa soglia. In questo caso, l'input elaborato non può fare riferimento a nessuna condizione normale incontrata in la fase di training e si è in presenza di una anomalia.

![](https://drive.google.com/uc?export=view&id=1dH6Isia2sKC5y0dADTtzCubK_lzNtgRf)


La proposta si colloca nella prima fase della catena delle emergenze, momento in cui emerge la situazione critica e occorre pianificare il primo intervento. Si tratta forse della fase più critica, perché una azione non tempestiva sia nella emersione della criticità sia nella sua risoluzione può complicare ulteriormente la situazione in essere.
La proposta nasce dall'idea che, nelle reti di distribuzione, le anomalie emergono prevalentemente sulla base di segnalazioni da parte dell’utente del servizio. Il monitoraggio automatico della rete di sensori e la disponibilità di tecniche di Machine Learning e Deep Learning per l’emersione delle anomalie, che sono efficaci e affidabili anche in contesti non supervisionati, rende tale processo più tempestivo, anticipando la segnalazione dell’utente e contenendo l’impatto del problema.


# Code

In [ ]:
!git clone https://github.com/softlab-unimore/SBDIOI40
!pip install -q -r SBDIOI40/requirements.txt

Cloning into 'SBDIOI40'...
remote: Enumerating objects: 447, done.
remote: Counting objects: 100% (447/447), done.
remote: Compressing objects: 100% (183/183), done.
remote: Total 447 (delta 255), reused 444 (delta 255), pack-reused 0
Receiving objects: 100% (447/447), 4.08 MiB | 8.43 MiB/s, done.
Resolving deltas: 100% (255/255), done.
     |████████████████████████████████| 153kB 6.9MB/s 


In [ ]:
import sys
sys.path.append('./SBDIOI40')

In [ ]:
import os
import numpy as np
import pandas as pd
import plotly.graph_objects as go

from timely.utils.manage_model import get_model, predict_anomaly
from timely.utils.tools import create_triplet_time_series, get_sliding_window_matrix

train_file = "./SBDIOI40/data/sample/series_state_1_1.csv"
train_file2 = "./SBDIOI40/data/sample/series_state_2_1.csv"
test_file = "./SBDIOI40/data/sample/series_state_all.csv"

assert os.path.isfile(train_file), 'No train selected'
assert os.path.isfile(test_file), 'No test selected'
assert os.path.isfile(train_file2), 'No new train selected'

model_type = 'cnn'
kernel = 180
stride = 1

# Anomaly Detection

Le serie temporali analizzate rappresentano i valori di accellerazione di un macchinario presi da 9 sensori durante le normali attività di lavoro in diverse condizioni operative. In particolare, ci sono 4 condizioni operative del macchinario di cui l'ultima dovuta a un guasto improvviso.

La seguente figura mostra in maniera compatta i 4 stati del macchinario (ogni 1200/1400 valori c'è un cambio di stato)

In [ ]:
#@title Machine state
# Read train file
print('4 machine states: ', os.path.basename(test_file))
ds = pd.read_csv(test_file)

fig = go.Figure()
for col in ds.columns:
  fig.add_trace(go.Scatter(x=ds.index, y=ds[col], name=col, opacity=0.8))
  
fig.show()

4 machine states:  series_state_all.csv


## Obiettivo

L'obiettivo di questa analisi è allenare un modello di Deep Learning nel riconoscere segnali appartenti a comportamenti noti, come normali, mentre cambiamenti, guasti, e altre condizioni operative come anomalie.

In particolare vengono mostrate di seguito due analisi riguardante l'identificazione di cambi di stato del macchinario:
1. "One normal behaviour": Il modello viene allenato solo un comportamento normale, andando a riconoscere eventuali deviazioni da esso
2. Two normal behaviour": Il modello viene allenato su due condzioni operative, mostrato la possibilità di imparare più pattern di comportamento.

Questi algoritmi possono essere applicati in diversi domini, dove l'obiettivo è andare a riconoscere qualcosa di nuovo. 

## One normal behaviour

In [ ]:
#@title Normal behaviour
# Read train file
print('Read train file: ', os.path.basename(train_file))
ds_train = pd.read_csv(train_file)

# Create training set
x_train = get_sliding_window_matrix(ds_train.values, kernel, stride)

ds = ds_train.copy()
fig = go.Figure()
for col in ds.columns:
  fig.add_trace(go.Scatter(x=ds.index, y=ds[col], name=col, opacity=0.8))
  
fig.show()

Read train file:  series_state_1_1.csv


In [ ]:
#@title Model training
%%capture

# Model initialization
model = get_model(model_type)

# Training
print("Training...")
model.fit(x_train)

In [ ]:
#@title Search anomalies
%%capture

print("Read Test File: ", os.path.basename(test_file))
ds_test = pd.read_csv(test_file)

print('Search...')
y_pred = predict_anomaly(ds_test, model, kernel, with_skip=False)

# Encoding results into triplet formats
results = create_triplet_time_series(y_pred, with_support=True)


In [ ]:
#@title Visualize founded anomalies
results = pd.DataFrame(results)
results = results[results['support'] > kernel]

print('\nFound anomalies at')
display(results)

# Visualize founded anomalies
fig = go.Figure()
for col in ds_test.columns:
  fig.add_trace(go.Scatter(x=ds_test.index, y=ds_test[col], name=col, opacity=0.8))
  

shapes = []

for key, val in results.iterrows():
  shapes.append(
      go.layout.Shape(
          type="rect", xref="x", yref="paper",
          x0=val['start'], y0=0,
          x1=val['end'], y1=1,
          fillcolor="LightSalmon", opacity=0.5,
          layer="below", line_width=0
      )
  )

fig.update_layout(shapes=shapes)
fig.show()


Found anomalies at


feature  start   end  support
0  features   1344  5387     4043

In questo esperimento, dopo aver allenato il modello a imparare lo stato visto precedentemente (*stato 1 *salvato nel file "*series_state_1_1.csv*"), abbiamo cercato le *anomalie* nella serie temporale contenente tutti e 4 gli stati del macchinario. Come si vede dal grafico, l'algoritmo è in grado distinguere correttamente i comportamenti già visti (*stato 1*), da quelli nuovi (*stato 2, 3 e 4*), i quali sono evidenziati in rosso.

Come si può notare l'algorimto è in grado di imparare i pattern di normalità del singolo stato selezionato, andando ad evidenziare deviazioni da esso.

## Two normal behaviour

In [ ]:
#@title Second normal behaviour
# Read train file
print('Read another train file: ', os.path.basename(train_file2))
ds_train2 = pd.read_csv(train_file2)

# Create training set
x_train2 = get_sliding_window_matrix(ds_train2.values, kernel, stride)

new_x_train = np.vstack([x_train, x_train2])

Read another train file:  series_state_2_1.csv


In [ ]:
#@title Model training multi behaviors
%%capture

# Model initialization
model = get_model(model_type)

# Training
print("Training...")
model.fit(new_x_train)

In [ ]:
#@title Search anomalies
%%capture
print("Read Test File: ", os.path.basename(test_file))
ds_test = pd.read_csv(test_file)

print('Search...')
y_pred = predict_anomaly(ds_test, model, kernel, with_skip=False)

# Encoding results into triplet formats
results = create_triplet_time_series(y_pred, with_support=True)




In [ ]:
#@title Visualize founded anomalies
results = pd.DataFrame(results)
results = results[results['support'] > kernel]

print('\nFound anomalies at')
display(results)

# Visualize founded anomalies
fig = go.Figure()
for col in ds_test.columns:
  fig.add_trace(go.Scatter(x=ds_test.index, y=ds_test[col], name=col, opacity=0.8))
  

shapes = []

for key, val in results.iterrows():
  shapes.append(
      go.layout.Shape(
          type="rect", xref="x", yref="paper",
          x0=val['start'], y0=0,
          x1=val['end'], y1=1,
          fillcolor="LightSalmon", opacity=0.5,
          layer="below", line_width=0
      )
  )

fig.update_layout(shapes=shapes)
fig.show()


Found anomalies at


feature  start   end  support
6  features   2877  5387     2510

In questo esperimento, dopo aver allenato il modello a imparare due stati di normalità del macchinario (*stato 1 e 2* con i file "*series_state_1_1.csv*" e "*series_state_2_1.csv*" rispettivamente), abbiamo rieseguito l'algoritmo per cercare i cambiamenti di stato. Come si vede in figura, l'algoritmo è in grado di riconoscere come anomali solamente gli *stati 3 e 4*.  

Come si può notare l'algorimto è in grado di imparare correttamente più pattern di normalità dei segnali selezionati, andando ad evidenziare deviazioni da essi.

Ovviamente questo algoritmo è stato progetto per essere resistente al rumore del segnale normale, un esempios si può vedere intorno ai punti 1300/14000 che ci sono sbalzi di accellerazione dovuti a un errore nella misurazione del segnale per una scarica elettrica improvvisa.